# XML example and exercise
****
+ study examples of accessing nodes in XML tree structure  
+ work on exercise to be completed and submitted
****
+ reference: https://docs.python.org/2.7/library/xml.etree.elementtree.html
+ data source: http://www.dbis.informatik.uni-goettingen.de/Mondial
****

In [1]:
from xml.etree import ElementTree as ET
import numpy as np #will require later for use of np.nan
import pandas as pd #will require later for building dataframes

## XML example

+ for details about tree traversal and iterators, see https://docs.python.org/2.7/library/xml.etree.elementtree.html

In [2]:
document_tree = ET.parse( './data/mondial_database_less.xml' )

In [3]:
dir(document_tree) #checking the methods available to call in ElementTree

['__class__',
 '__delattr__',
 '__dict__',
 '__doc__',
 '__format__',
 '__getattribute__',
 '__hash__',
 '__init__',
 '__module__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 '_root',
 '_setroot',
 'find',
 'findall',
 'findtext',
 'getiterator',
 'getroot',
 'iter',
 'iterfind',
 'parse',
 'write',
 'write_c14n']

In [4]:
# print names of all countries
for child in document_tree.getroot():
    print child.find('name').text

Albania
Greece
Macedonia
Serbia
Montenegro
Kosovo
Andorra


In [5]:
# print names of all countries and their cities
for element in document_tree.iterfind('country'):
    print '* ' + element.find('name').text + ':',
    capitals_string = ''
    for subelement in element.getiterator('city'):
        capitals_string += subelement.find('name').text + ', '
    print capitals_string[:-2]

* Albania: Tirana, Shkodër, Durrës, Vlorë, Elbasan, Korçë
* Greece: Komotini, Kavala, Athina, Peiraias, Peristeri, Acharnes, Patra, Kozani, Kerkyra, Ioannina, Thessaloniki, Iraklio, Chania, Ermoupoli, Rhodes, Tripoli, Lamia, Chalkida, Larissa, Volos, Mytilini, Karyes
* Macedonia: Skopje, Kumanovo
* Serbia: Beograd, Novi Sad, Niš
* Montenegro: Podgorica
* Kosovo: Prishtine
* Andorra: Andorra la Vella


****
## XML exercise

Using data in 'data/mondial_database.xml', the examples above, and refering to https://docs.python.org/2.7/library/xml.etree.elementtree.html, find

1. 10 countries with the lowest infant mortality rates
2. 10 cities with the largest population
3. 10 ethnic groups with the largest overall populations (sum of best/latest estimates over all countries)
4. name and country of a) longest river, b) largest lake and c) airport at highest elevation

In [6]:
document = ET.parse( './data/mondial_database.xml' )

## Start of Josh Mayer Analysis & Answers

In [7]:
#load into root var for ease
root = document.getroot()

In [8]:
#Checking the structure of the XML file
for elem in root.iter() :
    print elem.tag, elem.attrib

mondial {}
country {'memberships': 'org-BSEC org-CEI org-CD org-SELEC org-CE org-EAPC org-EBRD org-EITI org-FAO org-IPU org-IAEA org-IBRD org-ICC org-ICAO org-ICCt org-Interpol org-IDA org-IFRCS org-IFC org-IFAD org-ILO org-IMO org-IMF org-IOC org-IOM org-ISO org-OIF org-ITU org-ITUC org-IDB org-MIGA org-NATO org-OSCE org-OPCW org-OAS org-OIC org-PCA org-UN org-UNCTAD org-UNESCO org-UNIDO org-UPU org-WCO org-WFTU org-WHO org-WIPO org-WMO org-UNWTO org-WTO', 'area': '28750', 'car_code': 'AL', 'capital': 'cty-Albania-Tirane'}
name {}
population {'measured': 'est.', 'year': '1950'}
population {'measured': 'est.', 'year': '1960'}
population {'measured': 'est.', 'year': '1970'}
population {'measured': 'est.', 'year': '1980'}
population {'measured': 'est.', 'year': '1990'}
population {'year': '1997'}
population {'measured': 'est.', 'year': '2000'}
population {'measured': 'census', 'year': '2001'}
population {'measured': 'census', 'year': '2011'}
population_growth {}
infant_mortality {}
gdp_t

## Problem #1: 10 countries with the lowest infant mortality rates

In [9]:
#initialize lists for later building pandas dataframe
country_list = []
infant_mort_list = []

In [10]:
#Iterate over root, build lists that contain country names and infant mortality rates
for child in root :
    if child.find('infant_mortality') != None :
        #print child.find('name').text, float(child.find('infant_mortality').text)
        country_list.append(child.find('name').text)
        infant_mort_list.append(float(child.find('infant_mortality').text))
    else :
        #print child.find('name').text, float(0)
        country_list.append(child.find('name').text)
        infant_mort_list.append(np.nan) #loading NaN values if there is no infant mortality rate

In [11]:
#build pandas dataframe for analysis
df = pd.DataFrame({'Country' : country_list, 'Infant_Mortality' : infant_mort_list})

In [12]:
#Filter out any countries with NaN in 'Infant_Mortality' col 
df = df[np.isnan(df['Infant_Mortality']) == False]

## Answer #1 Below

In [13]:
#Group by country, isolate the 10 countries with lowest infant mortality rate
df.groupby(['Country', 'Infant_Mortality']).head().sort_values(by='Infant_Mortality', ascending=True).head(10)

Country  Infant_Mortality
38           Monaco              1.81
98            Japan              2.13
117         Bermuda              2.48
36           Norway              2.48
106       Singapore              2.53
37           Sweden              2.60
10   Czech Republic              2.63
78        Hong Kong              2.73
79            Macao              3.13
44          Iceland              3.15

## Problem #2: 10 cities with the largest population

In [14]:
#initialize empty lists for appending data and building pandas dataframes
city_names = []
pop_data = []

In [15]:
# print names of all cities and their populations
# since the population data is from different years for each city, take the most recent year's population
# for comparison
for element in root.iterfind('country') :
    for subelement in element.getiterator('city') :
        if subelement.find('population') != None :
            #print subelement.find('name').text, subelement.find('population[last()]').text
            city_names.append(subelement.find('name').text)
            pop_data.append(int(subelement.find('population[last()]').text))
        else :
            #print subelement.find('name').text, np.nan
            city_names.append(subelement.find('name').text)
            pop_data.append(np.nan)

In [16]:
#verify that the lists are the same lengths
print len(city_names), len(pop_data)

3380 3380


In [17]:
#Initialize city, population data frame
df2 = pd.DataFrame({'City' : city_names, 'Population' : pop_data})

In [19]:
#Filter out the NaN values
df2 = df2[np.isnan(df2['Population']) == False]

In [20]:
#Verify that we have matching non-null values for both City and Population
df2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3050 entries, 0 to 3379
Data columns (total 2 columns):
City          3050 non-null object
Population    3050 non-null float64
dtypes: float64(1), object(1)
memory usage: 71.5+ KB


## Answer #2 Below

In [21]:
df2.sort_values(by='Population', ascending=False).head(10)

City  Population
1341   Shanghai  22315474.0
771    Istanbul  13710512.0
1527     Mumbai  12442373.0
479      Moskva  11979529.0
1340    Beijing  11716620.0
2810  São Paulo  11152344.0
1342    Tianjin  11090314.0
1064  Guangzhou  11071424.0
1582      Delhi  11034555.0
1067   Shenzhen  10358381.0

## Problem #3: 10 ethnic groups with the largest overall populations (sum of best/latest estimates over all countries)

In [22]:
#Initialize clean lists
ethnic_pop = []
ethnic_groups = []

In [23]:
#Iterating over country, population, and ethnic group to build the data set
#Perform some minor calculations to derive integer for ethnic group population per country
for element in root.iterfind('country') :
    #print element.find('name').text, int(element.find('population[last()]').text)
    for ele2 in element.findall('ethnicgroup') :
        #print ele2.text, float(ele2.get('percentage'))/100
        #print ele2.text, '%.f' % (float(element.find('population[last()]').text) * float(ele2.get('percentage'))/100)
        ethnic_groups.append(ele2.text)
        ethnic_pop.append(int('%.f' % (float(element.find('population[last()]').text) * float(ele2.get('percentage'))/100)))

Unfortunately the data is not the best, the sum of the ethnic group percentages by country does not equal 100% meaning that if we were to sum the total population by country it would NOT equal the sum of the ethnic percentages * population. 

In [24]:
#check len
print len(ethnic_pop),  len(ethnic_groups)

628 628


In [25]:
#build our data frame for analysis
df3 = pd.DataFrame({'Ethnic_Groups' : ethnic_groups, 'Population' : ethnic_pop})

In [26]:
#confirm we have 'Population' as integers
df3.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 628 entries, 0 to 627
Data columns (total 2 columns):
Ethnic_Groups    628 non-null object
Population       628 non-null int64
dtypes: int64(1), object(1)
memory usage: 9.9+ KB


## Answer #3

In [27]:
#At last, our answer to problem #3: 10 ethnic groups with the largest overall populations
#sum of best/latest estimates over all countries 
df3.groupby('Ethnic_Groups').sum().sort_values(by='Population', ascending=False).head(11)

Population
Ethnic_Groups            
Han Chinese    1245058800
Indo-Aryan      871815583
European        494872221
African         318325121
Dravidian       302713744
Mestizo         157734355
Bengali         146776917
Russian         131856994
Japanese        126534212
Malay           121993550
Javanese        113538877

## Problem #4: name and country of a) longest river, b) largest lake and c) airport at highest elevation

In [28]:
#Checking the structure of the XML file
for elem in root.iter() :
    print elem.tag, elem.attrib

mondial {}
country {'memberships': 'org-BSEC org-CEI org-CD org-SELEC org-CE org-EAPC org-EBRD org-EITI org-FAO org-IPU org-IAEA org-IBRD org-ICC org-ICAO org-ICCt org-Interpol org-IDA org-IFRCS org-IFC org-IFAD org-ILO org-IMO org-IMF org-IOC org-IOM org-ISO org-OIF org-ITU org-ITUC org-IDB org-MIGA org-NATO org-OSCE org-OPCW org-OAS org-OIC org-PCA org-UN org-UNCTAD org-UNESCO org-UNIDO org-UPU org-WCO org-WFTU org-WHO org-WIPO org-WMO org-UNWTO org-WTO', 'area': '28750', 'car_code': 'AL', 'capital': 'cty-Albania-Tirane'}
name {}
population {'measured': 'est.', 'year': '1950'}
population {'measured': 'est.', 'year': '1960'}
population {'measured': 'est.', 'year': '1970'}
population {'measured': 'est.', 'year': '1980'}
population {'measured': 'est.', 'year': '1990'}
population {'year': '1997'}
population {'measured': 'est.', 'year': '2000'}
population {'measured': 'census', 'year': '2001'}
population {'measured': 'census', 'year': '2011'}
population_growth {}
infant_mortality {}
gdp_t

In [35]:
#building empty arrays for appending data and building pandas dataframes
countries = []
rivers = []
r_length = []

In [36]:
#Iterate and append river, country name, and river length to empty lists
for element in root.iterfind('river') :
    if element.find('length') != None :
        #print element.find('name').text, element.get('country'), element.find('length').text
        countries.append(element.get('country'))
        rivers.append(element.find('name').text)
        r_length.append(int('%.f' % float(element.find('length').text)))
    else : 
        #print element.find('name').text, element.get('country'), 0
        countries.append(element.get('country'))
        rivers.append(element.find('name').text)
        r_length.append(0)

In [37]:
print len(countries), len(rivers), len(r_length)

238 238 238


In [38]:
rivers_df = pd.DataFrame({'Countries' : countries, 'River' : rivers, 'Length' : r_length})

In [39]:
rivers_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 238 entries, 0 to 237
Data columns (total 3 columns):
Countries    238 non-null object
Length       238 non-null int64
River        238 non-null object
dtypes: int64(1), object(2)
memory usage: 5.6+ KB


## Answer 4a: name and country of a) longest river

In [40]:
#Answer to 4a: Longest river is Amazonas with length 6448 spanning multiple countries
rivers_df.sort_values(by='Length', ascending=False).head(1)

Countries  Length     River
174  CO BR PE    6448  Amazonas

## Problem 4b: Largest Lake

In [41]:
#Initialize empty sets
lake_country = []
lake_name = []
lake_area = []

In [42]:
#Building data for largest lake, similar to the others we are going to iterate over the 'lake' handle, 
#and then check if we have any null values
for element in root.iterfind('lake') :
    if (element.get('country') != None) & (element.find('name') != None) & (element.find('area') != None) :
        #print element.get('country'), element.find('name').text, int('%.f' % float(element.find('area').text))
        lake_country.append(element.get('country'))
        lake_name.append(element.find('name').text)
        lake_area.append(int('%.f' % float(element.find('area').text)))
    else :
        #print element.get('country'), element.find('name').text, 0
        lake_country.append(element.get('country'))
        lake_name.append(element.find('name').text)
        lake_area.append(0)

In [43]:
#check list lengths and verify area is stored as type = int
print len(lake_country), len(lake_name), len(lake_area)
print type(lake_area[0])

141 141 141
<type 'int'>


In [44]:
#build our pandas dataframe for analysis
lake_df = pd.DataFrame({'Country' : lake_country, 'Lake_Name' : lake_name, 'Area' : lake_area})

In [45]:
#let's verify the dataframe is complete
lake_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 141 entries, 0 to 140
Data columns (total 3 columns):
Area         141 non-null int64
Country      141 non-null object
Lake_Name    141 non-null object
dtypes: int64(1), object(2)
memory usage: 3.4+ KB


## Answer to 4b below. Largest lake in the world!

In [46]:
#finally, produce the country, name, and area (km**2) of the largest lake in the world
lake_df.sort_values(by='Area', ascending=False).head(1)

Area         Country    Lake_Name
54  386400  R AZ KAZ IR TM  Caspian Sea

## Problem 4c: c) airport at highest elevation

In [52]:
#Initialize empty sets
airport_country = []
airport_name = []
airport_elevation = []

In [53]:
#Building data for largest lake, similar to the others we are going to iterate over the 'lake' handle, 
#and then check if we have any null values
for element in root.iterfind('airport') :
    if (element.get('country') != None) & (element.find('name') != None) & (element.find('elevation') != None) :
        print element.get('country'), element.find('name').text, int('%.f' % float(element.find('elevation').text))
        airport_country.append(element.get('country'))
        airport_name.append(element.find('name').text)
        airport_elevation.append(int('%.f' % float(element.find('elevation').text)))
    else :
        print element.get('country'), element.find('name').text, 0
        airport_country.append(element.get('country'))
        airport_name.append(element.find('name').text)
        airport_elevation.append(0)

AFG Herat 977
AFG Kabul Intl 1792
AL Tirana Rinas 38
DZ Cheikh Larbi Tebessi 811
DZ Batna Airport 822
DZ Soummam 6
DZ Tamanrasset 1377
DZ Biskra 88
DZ Mohamed Boudiaf Intl 691
DZ Ain Arnat Airport 1024
DZ Es Senia 90
DZ Noumerat 461
DZ Annaba 5
DZ Houari Boumediene 25
DZ Zenata 248
AMSA Pago Pago Intl 10
ANG Lubango 1762
ANG Cabinda 20
ANG Menongue 1363
ANG Luanda 4 De Fevereiro 74
ANG Huambo 1703
AXA Wallblake 39
AG V C Bird Intl 19
RA La Rioja 438
RA Jujuy 920
RA Comandante Espora 75
RA Teniente Benjamin Matienzo 456
RA San Luis 710
RA Santiago del Estero 200
RA Sauce Viejo 17
RA Corrientes 62
RA Presidente Peron 273
RA Salta 1246
RA Aeroparque Jorge Newbery 5
RA Ministro Pistarini 20
RA Ushuaia Malvinas Argentinas 22
RA Formosa 59
RA Posadas 131
RA Rosario 26
RA Resistencia 53
RA Rio Gallegos 19
RA Comodoro Rivadavia 58
RA Mar Del Plata 22
RA El Plumerillo 704
RA Ambrosio L V Taravella 489
ARM Zvartnots 865
ARU Reina Beatrix Intl 18
AUS Melbourne Intl 132
AUS Sydney Intl 6
AUS Cairn

TypeError: float() argument must be a string or a number

In [54]:
#check list lengths and verify area is stored as type = int
print len(airport_country), len(airport_name), len(airport_elevation)
print type(airport_elevation[0])

 183 183 183
<type 'int'>


In [55]:
#Build pandas dataframe for analysis
airport_df = pd.DataFrame({'Country' : airport_country, 'Airport_Name' : airport_name, 'Elevation' : airport_elevation})

In [56]:
#let's verify the dataframe is complete
airport_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 183 entries, 0 to 182
Data columns (total 3 columns):
Airport_Name    183 non-null object
Country         183 non-null object
Elevation       183 non-null int64
dtypes: int64(1), object(2)
memory usage: 4.4+ KB


## Answer 4c : airport at highest elevation

In [57]:
#finally, produce the country, airport name, and elevation (km) of the highest airport in the world
airport_df.sort_values(by='Elevation', ascending=False).head(1)

Airport_Name Country  Elevation
80  El Alto Intl     BOL       4063